<a href="https://colab.research.google.com/github/tae898/DeepLearning/blob/master/Chapter06_Deep_Feedforward_Networks.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Clone the repo, install the package, download data, and extract them.

Don't run `pip install -r requirements.txt` from the original installation guide. They are made for python3.7, but colab still uses python3.6. We'll install the necessary packages here on the fly.

In [1]:
%cd /content
!git clone https://github.com/leolani/cltl-face-all
!cd cltl-face-all/ && pip install .
!pip install omegaconf==2.0.5
!pip install tqdm av

!git clone https://github.com/cltl/ma-communicative-robots.git

# Download the annotations and stuff
!wget https://raw.githubusercontent.com/declare-lab/MELD/master/data/MELD/train_sent_emo.csv
!wget https://raw.githubusercontent.com/declare-lab/MELD/master/data/MELD/dev_sent_emo.csv
!wget https://raw.githubusercontent.com/declare-lab/MELD/master/data/MELD/test_sent_emo.csv

/content
Cloning into 'cltl-face-all'...
remote: Enumerating objects: 157, done.
remote: Counting objects: 100% (157/157), done.
remote: Compressing objects: 100% (142/142), done.
remote: Total 157 (delta 32), reused 134 (delta 13), pack-reused 0
Receiving objects: 100% (157/157), 20.01 MiB | 10.33 MiB/s, done.
Resolving deltas: 100% (32/32), done.
Processing /content/cltl-face-all
  Created wheel for cltl-face-all: filename=cltl_face_all-0.0.0-cp36-none-any.whl size=53234 sha256=acc0a4f21589221f10ded54a63030bb6b79695960f612d657611e2ea7ad8f7b3
  Stored in directory: /root/.cache/pip/wheels/8d/71/f3/2db0b17856a0b395aaa04c8562716e0350cfc712cdd4b9947e
Successfully built cltl-face-all
     |████████████████████████████████| 276kB 6.8MB/s 
  Created wheel for PyYAML: filename=PyYAML-5.3.1-cp36-cp36m-linux_x86_64.whl size=44619 sha256=f3a2c864cacd7baacf31213f93dd9abdb6b622539ed1a21bda9c1bf32db139a0
  Stored in directory: /root/.cache/pip/wheels/a7/c1/ea/cf5bd31012e735dc1dfea3131a2d5eae7978b2

# Assess the data

The number of videos should be the same

In [2]:
import os
from glob import glob
import csv
import json


# Only the train_sent_emo is relevant to us since the smaller datasets
# are subset of the original train dataset.
annotation_path = 'train_sent_emo.csv'
        
vids_dir = "ma-communicative-robots/multimodal/smaller-dataset/"

datasets = {}
datasets['small'] = "ma-communicative-robots/multimodal/dataset-small.json"
datasets['medium'] = "ma-communicative-robots/multimodal/dataset-medium.json"
datasets['large'] = "ma-communicative-robots/multimodal/dataset-large.json"

for datasize in ['small', 'medium', 'large']:
    with open(datasets[datasize], 'r') as stream:
        datasets[datasize] = json.load(stream)

with open(annotation_path) as f:
    reader = csv.reader(f)
    annotations = list(reader)


# See if we have all of the videos
for datasize in ['small', 'medium', 'large']:
    for datatype in ['train', 'dev', 'test']:
        diautt_ = datasets[datasize][datatype]
        for diautt in diautt_:
            assert os.path.isfile(os.path.join(vids_dir, diautt))

# Find the corresponding speaker / emotion / sentiment from the annotations

vid2anno = {}
for row in annotations[1:]:
    SrNo, Utterance, Speaker, Emotion, Sentiment, Dialogue_ID,\
        Utterance_ID, Season, Episode, StartTime, EndTime = row

    if f"dia{Dialogue_ID}_utt{Utterance_ID}.mp4" not in str(os.listdir(os.path.join(vids_dir))):
        continue
    vid2anno[f"dia{Dialogue_ID}_utt{Utterance_ID}.mp4"] = \
        {'speaker':Speaker, 
         'emotion': Emotion, 
         'sentiment': Sentiment,
         'Utterance': Utterance}

for datasize in ['small', 'medium', 'large']:
    for datatype in ['train', 'dev', 'test']:
        diautt_ = datasets[datasize][datatype]
        for idx, diautt in enumerate(diautt_):
            
            datasets[datasize][datatype][idx] = \
                (diautt, vid2anno[diautt])

with open('datasets.json', 'w', encoding='utf8') as json_file:
    json.dump(datasets, json_file, ensure_ascii=False)

# Let's check out a couple of videos to see if our labeling is correct.

In [3]:
import random
chosen = random.choice(datasets['small']['train'])
print(chosen)

vidpath = os.path.join(vids_dir, chosen[0])
print(vidpath)

from IPython.display import HTML
from base64 import b64encode
mp4 = open(vidpath,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

HTML("""
<video width=1280 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

('dia151_utt12.mp4', {'speaker': 'Rachel', 'emotion': 'neutral', 'sentiment': 'neutral', 'Utterance': 'You’re right.'})
ma-communicative-robots/multimodal/smaller-dataset/dia151_utt12.mp4


# Instantiate the three classes we need.

In [4]:
from cltl_face_all.face_alignment import FaceDetection
from cltl_face_all.arcface import ArcFace
from cltl_face_all.agegender import AgeGender

fd = FaceDetection(device='cuda', face_detector='sfd')
ag = AgeGender(device='cpu')
af = ArcFace(device='cpu')

Downloading: "https://www.adrianbulat.com/downloads/python-fan/s3fd-619a316812.pth" to /root/.cache/torch/hub/checkpoints/s3fd-619a316812.pth


Downloading: "https://www.adrianbulat.com/downloads/python-fan/2DFAN4-11f355bf06.pth.tar" to /root/.cache/torch/hub/checkpoints/2DFAN4-11f355bf06.pth.tar



94773248/94765736 [==============================] - 2s 0us/step
[*] load ckpt from /usr/local/lib/python3.6/dist-packages/cltl_face_all/arcface/./pretrained_models/arc_res50/e_8_b_40000.ckpt


# Run over the images

In [ ]:
from tqdm.notebook import tqdm
import av
import numpy as np
import os
import shutil

!rm visual-features.zip
shutil.rmtree('visual-features', ignore_errors=True)
os.makedirs('visual-features', exist_ok=True)

for vidpath in tqdm(glob(os.path.join(vids_dir, '*.mp4'))):
    print(vidpath)

    diautt = os.path.basename(vidpath)
    to_dump = {}

    container = av.open(vidpath)

    for frame in tqdm(container.decode(video=0)):
        idx = frame.index
        to_dump[idx] = []
        numpy_RGB = np.array(frame.to_image())
        batch = numpy_RGB[np.newaxis, ...]
        bboxes = fd.detect_faces(batch)
        # print(f"number of faces detected in the frame {idx} is {len(bboxes[0])}")

        if len(bboxes[0]) == 0:
            continue

        landmarks = fd.detect_landmarks(batch, bboxes)

        faces = fd.crop_and_align(batch, bboxes, landmarks)
        faces = np.concatenate(faces, axis=0)
        embeddings = af.predict(faces)
        ages, genders = ag.predict(faces)

        # print(len(bboxes[0]), len(landmarks[0]), len(ages), len(genders), len(embeddings), len(faces))
        for bb, lm, a, g, emb, f in zip(bboxes[0], landmarks[0], ages, genders, embeddings, faces):
            x1, y1, x2, y2, prob = bb

            to_append = {'bbox': bb, 
                        'landmark': lm, 
                        'age': a,
                        'gender': g,
                        'embedding': emb,
                        'face': f}

            to_dump[idx].append(to_append)
        # print(len(to_dump), idx+1)

    np.save(os.path.join('visual-features', f"{diautt.replace('.mp4', '.npy')}" ), to_dump)

!zip -r visual-features.zip visual-features

rm: cannot remove 'visual-features.zip': No such file or directory


ma-communicative-robots/multimodal/smaller-dataset/dia335_utt3.mp4


/usr/local/lib/python3.6/dist-packages/cltl_face_all/face_alignment/matlab_cp2tform.py:84: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  r, _, _, _ = lstsq(X, U)



ma-communicative-robots/multimodal/smaller-dataset/dia111_utt16.mp4



ma-communicative-robots/multimodal/smaller-dataset/dia869_utt14.mp4


...


ma-communicative-robots/multimodal/smaller-dataset/dia271_utt3.mp4



ma-communicative-robots/multimodal/smaller-dataset/dia441_utt1.mp4



ma-communicative-robots/multimodal/smaller-dataset/dia851_utt0.mp4



ma-communicative-robots/multimodal/smaller-dataset/dia610_utt1.mp4



ma-communicative-robots/multimodal/smaller-dataset/dia351_utt13.mp4
